In [6]:
# importing libraries
from bs4 import BeautifulSoup
import requests
import urllib.request
import re

In [7]:
def crawler_panorama(urls: dict):
    index = 0
    result = []
    for url, pages in urls.items():
        req = requests.get(url)
        soup = BeautifulSoup(req.text, "lxml")
    
        for i in range(1, pages):
            req = requests.get(url+"/page/" +str(i))
            soup = BeautifulSoup(req.text, "lxml")
            news_links = soup.find_all("div", {'class':"np-archive-post-content-wrapper"})
    
            for idx,news in enumerate(news_links):
                news_dict = {}
                url_news = news.find('a').get('href')
                title_news= news.find('a').text

                #find news content in url
                req_news =  requests.get(url_news)
                soup_news = BeautifulSoup(req_news.text, "lxml")

                #find news content 
                news_content = soup_news.find('div', {'class':"entry-content"})

                #find paragraph in news content 
                p = news_content.find_all('p')
                content = ' '.join(item.text for item in p)

                #find tags
                news_tags = soup_news.find('div', {'class':"post-cats-list"})
                a = news_tags.find_all('a')
                tags = []
                for i in a:
                    tags.append(i.text)
                tags = ' '.join(i for i in tags)

                #find date and author
                news_author = soup_news.find('div', {'class':"entry-meta"})
                a = news_author.find_all('a')
                author = a[1].text
                #date = a[0].text
                
                date = soup_news.find('meta', {'itemprop':"datePublished"}).get("content")

                #wrap in dictionary 
                news_dict['id']=index
                news_dict['url'] = url_news
                news_dict['title'] = title_news
                news_dict['content'] = content
                news_dict['author'] = author
                news_dict['date'] = date
                news_dict['tags'] = tags
                news_dict['type_of_article'] = 'fake'
                result.append(news_dict)
                index += 1
         
    return result


In [8]:
panorama1 = crawler_panorama({'https://panorama.pub/category/news/politics': 74})

In [13]:
panorama2 = crawler_panorama({'https://panorama.pub/category/news/society': 189})
for t in panorama2:
     print(t)

{'id': 0, 'url': 'https://panorama.pub/28262-mutko-nagrazhdyon-ordenom-kutuzova.html', 'title': 'Мутко награждён орденом Кутузова', 'content': 'Заместитель председателя правительства по вопросам строительства и регионального развития Виталий Мутко награждён министерством спорта орденом Михаила Кутузова. Как говорится на сайте ведомства, прежде всего были оценены заслуги Мутко как функционера. Чиновник помог выиграть право на проведение и триумфально провести Олимпиаду в Сочи и первый в истории страны Чемпионат мира по футболу. «Он как Кутузов повёл наших в атаку и с каждым днём улучшал наши спортивные достижения. Мутко вдохновлялся сам и вдохновлял спортсменов на победы. Его усилиями страна поднялась на новый уровень, который сложно достигнуть многим другим», — сказал министр спорта Павел Колобков. Орденом Михаила Кутузова награждаются граждане России, замещающие должности государственной службы, «за особые личные заслуги перед Отечеством в деле государственного строительства, многолет

{'id': 1400, 'url': 'https://panorama.pub/9879-atamany-pozhalovalis.html', 'title': 'Атаманы Сетевого казачьего войска пожаловались на сокращение финансирования в 2019 году', 'content': 'Восемь атаманов Сетевого казачьего войска обратились к Госдуме с открытым письмом, в котором попросили увеличить государственные ассигнования на казачьи интернет-патрули в 2019 году. Сумма, выделенное веб-казакам из бюджета, по сравнению с прошлым годом уменьшилась на 9 млн. рублей, составив всего 802 млн. По словам атамана петербургского куреня Григория Жуковицкого, Сетевое войско в настоящее время является единственной в России организацией, занимающейся сохранением древних традиций отечественного интернет-казачества и надзором за нравственностью во всемирной сети. Веб-казаки занимаются поиском материалов, оскорбляющих религиозные или патриотические чувства в соцсетях и устраивают киберрасправу над опубликовавшими их лицами, после чего направляют соответствующие материалы в правоохранительные органы.

In [14]:
panorama3 = crawler_panorama({'https://panorama.pub/category/news/science': 15})

In [15]:
panorama4 = crawler_panorama({'https://panorama.pub/category/news/economics': 13})

In [16]:
panorama = []
for i in (panorama1, panorama2, panorama3, panorama4):
  panorama.extend(i)

In [17]:
def crawler_ria(urls: list, links):
    index = 0
    result = []
    for url in urls:
        req = requests.get(url)
        soup = BeautifulSoup(req.text, "lxml")
    
        for i in range(links):
            news_links = soup.find_all("div", {'class':"list-item__content"})
#             print(news_links)
            
            for idx,news in enumerate(news_links):
                news_dict = {}
                url_news = news.find('a').get('href')
#                 print(url_news)
                
                #find news content in url
                if not 'https://' in url_news:
                    url_news = 'https://ria.ru/' + url_news
                req_news =  requests.get(url_news)
                soup_news = BeautifulSoup(req_news.text, "lxml")
                title_news = soup_news.find('title').text.split('- ')[0]
#                 tags = soup_news.find('script', dataLayer["page_tags"])
                date = soup_news.find('title').text.split('- ')[1].split(', ')[1]
                news_tags = soup_news.find('div', {'class':'endless'})
#                 print(news_tags)
                tags = news_tags.find('div', {'class':'endless__item'}).get('data-analytics-tags')
#                 print(tags)
#                 print(soup_news)
                
                content = ''
                news_content = soup_news.find_all('div', {'class':'article__text'})
                for c in news_content:
                    content += c.text
                
#                 news_tags = soup_news.find('div', {'class':'endless'})
#                 tags = news_tags.find('div', {'class':'endless__item'}).get('data-analytics-tags')
#                 print(tags)
                
#                 news_tags = soup_news.find('span', {'class':"category-button np-cat-14"})
#                 a = news_date.find_all('a')
#                 tags = ' '.join(item.text for item in a)

                #wrap in dictionary 
                news_dict['id']=index
                news_dict['url'] = url_news
                news_dict['title'] = title_news
                news_dict['content'] = content
                news_dict['author'] = 'None'
                news_dict['date'] = date
                news_dict['tags'] = tags
                news_dict['type_of_article'] = 'real'
                result.append(news_dict)
                index += 1
         
#             news_page = soup.find('div', {'class':"list-more"}).get("data-url")
#             req = requests.get(news_page)
#             soup = BeautifulSoup(req.text, "lxml")
                
        return result

In [18]:
ria1 = crawler_ria(['https://ria.ru/politics/'], 36)

In [19]:
ria2 = crawler_ria(['https://ria.ru/society/'], 94)

In [20]:
ria3 = crawler_ria(['https://ria.ru/economy/'], 7)

In [21]:
ria4 = crawler_ria(['https://ria.ru/science/'], 6)

In [22]:
ria = []
for i in (ria1, ria2, ria3, ria4):
    ria.extend(i)

In [25]:
import sqlite3
 
conn = sqlite3.connect("Fake_News_DB.db")
cursor = conn.cursor()
 
cursor.execute("""CREATE TABLE fake_news
                  (id integer, url text, title text,
                   content text, author text, date text, 
                   tags text, type_of_article text)
               """)

In [26]:
panorama_news = [tuple(d.values()) for d in panorama]

cursor.executemany("INSERT INTO fake_news VALUES (?,?,?,?,?,?,?,?)", panorama_news)
conn.commit()

In [27]:
ria_news = [tuple(d.values()) for d in ria]
 
cursor.executemany("INSERT INTO fake_news VALUES (?,?,?,?,?,?,?,?)", ria_news)
conn.commit()

In [28]:
cursor.execute("SELECT content FROM fake_news")
print(cursor.fetchone())

('В Госдуму внесён законопроект о «Защите положительного имиджа России», текстом которого предусматриваются ограничения для граждан относительно контента, загружаемого на веб-ресурсах. По мнению законодателей, пользователям сети необходимо блокировать возможность загружать фото- и видеоматериалы, потенциально носящие негативную коннотацию в контексте России. В дополнительном подзаконном акте законодатели разъясняют список таких материалов. В частности, речь идёт о фото- и видеофайлах, демонстрирующих ветхие жилые и заброшенные здания, ненадлежащий внутренний интерьер квартир, неровности на тротуарах и автодорогах, места неконтролируемого скопления бытовых отходов. Дополнительно уделено внимание изображениям, компрометирующим граждан РФ. В сеть запретят выкладывать фото россиян с явно выраженным низким социальным статусом, в частности, набирающий популярность жанр пребывания граждан возле контейнеров с бытовыми отходами. За размещение в сети изображений, запрещённых законом, будет введе

In [29]:
conn.close()